In [1]:
import torch
import torch.nn as nn
torch.cuda.is_available()

True

In [2]:
from transformers import LlamaTokenizer, LlamaForCausalLM
from peft import get_peft_model, PeftConfig, PeftModel

loc = 'sqllama-out3'

config = PeftConfig.from_pretrained(loc)
print(config)


tokenizer = LlamaTokenizer.from_pretrained(
    "decapoda-research/llama-7b-hf")
   
tokenizer.pad_token_id = 0
tokenizer.padding_side = 'left'

model = LlamaForCausalLM.from_pretrained(
    "decapoda-research/llama-7b-hf",
    load_in_8bit=True,
    device_map="auto",
    torch_dtype=torch.float16
)

model = PeftModel.from_pretrained(
    model, loc,
    torch_dtype=torch.float16,
    device_map="auto"
    )

#model = prepare_model_for_int8_training(model)

#model = get_peft_model(model,config)

/home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: /opt/conda did not contain libcudart.so as expected! Searching further paths...
  warn(msg)
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'LLaMATokenizer'. 
The class this function is called from is 'LlamaTokenizer'.



===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please submit your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 113
CUDA SETUP: Loading binary /home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/bitsandbytes/libbitsandbytes_cuda113.so...
PeftConfig(peft_type='LORA', base_model_name_or_path='decapoda-research/llama-7b-hf', task_type='CASUAL_LM', inference_mode=True)


Loading checkpoint shards:   0%|          | 0/33 [00:00<?, ?it/s]

In [36]:
import random
import json

# defined by WikiSQL

agg_ops = ['', 'MAX', 'MIN', 'COUNT', 'SUM', 'AVG']
cond_ops = ['=', '>', '<', 'OP']
syms = ['SELECT', 'WHERE', 'AND', 'COL', 'TABLE', 'CAPTION', 'PAGE', 'SECTION', 'OP', 'COND', 'QUESTION', 'AGG', 'AGGOPS', 'CONDOPS']

def fix_repr(d,cols,types,tid):
    sel_index=d['sel'] 
    agg_index=d['agg']
    conditions=d['conds']
    col = cols[sel_index]
    rep = 'SELECT {agg} {sel} FROM {tid}'.format(
            agg=agg_ops[agg_index],
            sel=col,
            tid=tid
            )
    if conditions:
        cs = []
        for i, o, v in conditions:
            #print(i,cols)
            nm = cols[i]
            op = cond_ops[o]
            
            if types[i] in ['text']:
                val = f"\'{v}\'"
            else:
                val = v
            cs.append(f'{nm} {op} {val}')
        #print(cs)

        rep +=  ' WHERE ' + ' AND '.join(cs)
    
    return rep

tbl_cols = {}
tbl_types = {}
tbl_str = {}

prefix = 'Below is a question that describes a data request, paired with an input that describes a SQL table.  Write a SQL query that retrieves the data.'

def tbl_def_to_string(id, header, types):
    s = f'table: {id}\ncolumns: ' + ','.join(header)
    return s

with open('data/test.tables.jsonl') as f:
    for line in f:
        js = json.loads(line)
        id = js['id']
        hdr = js['header']
        ts = js['types']
        tbl_str[id] = tbl_def_to_string(id,hdr,ts)
        tbl_cols[id] = hdr
        tbl_types[id] = ts

q_s = []
a_s = []

with open('data/test.jsonl') as f:
    for line in f:
        js = json.loads(line)
        id = js['table_id']
        s = tbl_str[id]
        qst = js['question']
        nl = s + '\nQ: ' + qst + '\nA: '
        q_s.append(nl)

        sql = js['sql']
        a = fix_repr(sql,tbl_cols[id],tbl_types[id],id)
        a = a + "\nEND\n"
        a_s.append(a)

M = len(q_s)

data_txt = [q_s[i] + a_s[i] for i in range(M)]

for i in range(5):
    j = random.randint(0,M-1)
    print()
    print(data_txt[j]) 
        
   


table: 2-1646960-11
columns: Year,Association,Category,Nominee,Result
Q: What was the result in a year before 2013 that the nomination category was Presenter Talent Show?
A: SELECT  Result FROM 2-1646960-11 WHERE Year < 2013 AND Category = 'presenter talent show'
END


table: 2-14282690-12
columns: 102.,28 February,Friendly,Croatia,Austria
Q: What is the smallest number for 102 when Friendly of friendly, and an Austria of greece?
A: SELECT MIN 102. FROM 2-14282690-12 WHERE Friendly = 'friendly' AND Austria = 'greece'
END


table: 2-1265278-1
columns: Hindi,Romani,Domari,Lomavren,Persian
Q: What Domari word has the same meaning as the Hindi word pāñc?
A: SELECT  Domari FROM 2-1265278-1 WHERE Hindi = 'pāñc'
END


table: 2-13073611-3
columns: Place,Player,Country,Score,To par
Q: Name the player with score of 74-68-71=213
A: SELECT  Player FROM 2-13073611-3 WHERE Score = '74-68-71=213'
END


table: 2-12601456-2
columns: Rank,Year,Name,Moving from,Moving to
Q: When was the earliest year th

In [5]:
toks = [tokenizer(s) for s in data_txt]


In [6]:
import numpy as np
import pandas as pd

print(len(toks[0].input_ids))
lens = np.array([len(tok.input_ids) for tok in toks])
print(pd.DataFrame(lens).describe())

z = zip(q_s,lens)
q_red = [a for a,b in z if b < 100]
z = zip(a_s,lens)
a_red = [a for a,b in z if b < 100]

data_red = [q_red[i] + a_red[i] for i in range(len(q_red))]
print(len(data_red))



86
                  0
count  15878.000000
mean     101.114750
std       21.311681
min       62.000000
25%       87.000000
50%       97.000000
75%      109.000000
max      390.000000
8981


In [12]:
def get_query(q):
    
    toks = tokenizer(q , return_tensors='pt')
    ctoks = toks.input_ids.to('cuda')
    gen = model.generate(ctoks, max_length=100)
    return tokenizer.decode(gen[0])

M = len(q_red)

for _ in range(10):
    j = random.randint(0,M-1)
    qs = q_red[j]
    a = a_red[j]

    ma = get_query(qs)

    #print(qs)
    print('from model')
    print(ma)
    print()
    print('expected answer')
    print(a)


/home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/transformers/generation/utils.py:1412: UserWarning: You are calling .generate() with the `input_ids` being on a device type different than your model's device. `input_ids` is on cuda, whereas the model is on cpu. You may experience unexpected behaviors or slower generation. Please make sure that you have put `input_ids` to the correct device by calling for example input_ids = input_ids.to('cpu') before running `.generate()`.
  UserWarning,


ValueError: Expected a cuda device, but got: cpu

In [7]:
print('encoding tokens')
toks = tokenizer(q_red, return_tensors='pt', padding=True).to('cuda')
    
print('generating ids')
gen_ids = model.generate(**toks, max_length=100)
print('decoding ids')
res = tokenizer.batch_decode(gen_ids)


encoding tokens
generating ids


OutOfMemoryError: CUDA out of memory. Tried to allocate 10.69 GiB (GPU 0; 14.56 GiB total capacity; 12.15 GiB already allocated; 1.35 GiB free; 12.45 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

In [7]:
model.eval()

def get_query(q):
    with torch.no_grad():
        toks = tokenizer(q , return_tensors='pt')
        ctoks = toks.input_ids.to('cuda')
        gen = model.generate(ctoks, max_length=100)
        return tokenizer.decode(gen[0])



model_data = []

M = len(q_red)

for i in range(M):
    if i % 10 == 0:
        print(f'processing question {i}')

    q = q_red[i]
    a = a_red[i]
    ma = get_query(q)
    model_data.append((q,a,ma))
    


processing question 0


/home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/transformers/generation/utils.py:1220: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co/docs/transformers/main_classes/text_generation)
  "You have modified the pretrained model configuration to control generation. This is a"


processing question 10
processing question 20
processing question 30
processing question 40
processing question 50
processing question 60
processing question 70
processing question 80
processing question 90
processing question 100
processing question 110
processing question 120
processing question 130
processing question 140
processing question 150
processing question 160
processing question 170
processing question 180
processing question 190
processing question 200
processing question 210
processing question 220
processing question 230
processing question 240
processing question 250
processing question 260
processing question 270
processing question 280
processing question 290
processing question 300
processing question 310
processing question 320
processing question 330
processing question 340
processing question 350
processing question 360
processing question 370
processing question 380
processing question 390
processing question 400
processing question 410
processing question 420
p

In [1]:
import pickle

fn ='inf3.pkl'

with open(fn,'wb') as f:
    pickle.dump(model_data,f)

NameError: name 'model_data' is not defined

In [62]:
import re
fn = 'inf2.pkl'

# defined by WikiSQL

agg_ops = ['', 'MAX', 'MIN', 'COUNT', 'SUM', 'AVG']
cond_ops = ['=', '>', '<', 'OP']
syms = ['SELECT', 'WHERE', 'AND', 'COL', 'TABLE', 'CAPTION', 'PAGE', 'SECTION', 'OP', 'COND', 'QUESTION', 'AGG', 'AGGOPS', 'CONDOPS']


with open(fn,'rb') as f:
    test_data = pickle.load(f)

def parse_sel(toks):
    t = 'N/A'
    try:
        t = toks[1].upper()
        if t in agg_ops:
            t = toks[2].upper()
    except:
        pass
    return t

def parse_table(toks):
    s = ''
    for i in range(len(toks)-1):
        if toks[i].lower() == 'from':
            s = toks[i+1]
    return s   

def parse_agg(toks):
    i = -1
    try:
        agg = toks[1].upper()
        if agg in agg_ops:
            i = agg_ops.index(agg)
    except:
        pass
    return i

def parse_conds(toks,val_to_lower=False):
    
    conds = set()
    for i in range(len(toks)-3):
        if toks[i].lower() in ['where','and']:
            col = toks[i+1].lower()
            op = toks[i+2]
            op_id = -1
            if op in cond_ops:
                op_id = cond_ops.index(op)
            val = toks[i+3]
            if val_to_lower:
                val = val.lower()
            conds.add((col,op_id,val))
    return conds
        
cs = 0
ct = 0
ca = 0
cc = 0
c = 0

case_sens = True

M = len(test_data)
#print(M)

for i in range(M):
    s = test_data[i][2]
    try:
        m = re.search('A:((.|\n)*?)END',s)
        s = m.group(1).strip()
    except:
        pass
    
    sa = test_data[i][1][0:-5]
    toks = s.split()
    toksa = sa.split()
    #print(s + " | " + sa)
    sel = parse_sel(toks)
    sela = parse_sel(toksa)
    tbl = parse_table(toks)
    tbla = parse_table(toksa)
    agg = parse_agg(toks)
    agga = parse_agg(toksa)
    conds = parse_conds(toks,val_to_lower= not case_sens)
    condsa = parse_conds(toksa,val_to_lower= not case_sens)
    bs = sel==sela
    bt = tbl==tbla
    ba = agg==agga
    bc = conds==condsa
    if bs:
        cs += 1
    if bt:
        ct += 1
    if ba:
        ca += 1
    if bc:
        cc += 1

    if bs and bt and ba and bc:
        c += 1
    
    #print(sel + " | " + sela + " | " + str(sel==sela))
    #print(tbl + " | " + tbla + " | " + str(tbl==tbla))
    #print(str(agg) + " | " + str(agga) + " | " + str(agg==agga)) 
    #print(str(conds) + " | " + str(condsa) + " | " + str(conds==condsa))

print(f'case sensitive literals: {case_sens}')
print(f'test set size: {M}')
print(f'correct select col: {cs/M*100:.2f}%')
print(f'correct agg: {ca/M*100:.2f}%')
print(f'correct tbl: {ct/M*100:.2f}%')
print(f'correct conds: {cc/M*100:.2f}%')
print(f'correct query: {c/M*100:.2f}%')






case sensitive literals: True
test set size: 8981
correct select col: 86.84%
correct agg: 89.31%
correct tbl: 95.71%
correct conds: 67.38%
correct query: 57.14%
